In [11]:
from __future__ import annotations
import data_reader
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler 
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, Dataset
from tqdm.notebook import tqdm
import copy
import plotly.express as px

In [ ]:
!pip install pandas==1.5.2

     |████████████████████████████████| 12.2 MB 11 kB/s s eta 0:00:01
  Attempting uninstall: pandas
    Found existing installation: pandas 1.5.3
    Uninstalling pandas-1.5.3:
      Successfully uninstalled pandas-1.5.3


# Data pre-processing

## Read data from files

In [2]:
consumption, weather, joined = data_reader.read_consumption_and_weather()

Holes by length and occurrences in column NO3:
holes
1        1
dtype: int64
Filling holes up to length 3
Any remaining holes after interpolation? False


## Outliers and anomalies
There doesn't look like there are any clear outliers, and the data can probably be used as it is

In [3]:
data_reader.plot_consumption_and_weather(joined)


ModuleNotFoundError: No module named 'plotly.validators.layout'

In [4]:
TARGET_VARIABLE = "consumption"

In [5]:
for area in data_reader.mbas:
    # Remember to override this to avoid data leakage
    joined[(area, "previous_y")] = joined[(area, TARGET_VARIABLE)].shift(1)
    joined[(area, "moving_24_avg_y")] = joined[(area, TARGET_VARIABLE)].rolling(24).mean()

training, validation = joined[:-1440], joined[-1440: -1]

scaler = StandardScaler()
training_ft = scaler.fit_transform(training)
validation_ft = scaler.transform(validation)

train = pd.DataFrame(training_ft, columns=training.columns, index=training.index)

val = pd.DataFrame(validation_ft, columns=validation.columns, index=validation.index)

for df in [train, val]:
    for area in data_reader.mbas:
        df[(area, "sin_h")] = np.sin(2*np.pi *df.index.hour / 24)
        df[(area, "cos_h")] = np.cos(2*np.pi *df.index.hour / 24)
        df[(area, "sin_day")] = np.sin(2*np.pi *df.index.dayofweek / 7)
        df[(area, "cos_day")] = np.cos(2*np.pi *df.index.dayofweek / 7)
        df[(area, "sin_dayofyear")] = np.sin(2*np.pi *df.index.dayofyear / 365)
        df[(area, "cos_dayofyear")] = np.cos(2*np.pi *df.index.dayofyear / 365)

In [24]:
class EnergyDataset(Dataset):
    def __init__(self, x, y=None):
        self.x = x
        self.y = y
        self.type = type
        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
            

    def __len__(self):
        return len(self.x) - 48

    def __getitem__(self, idx):
        if self.y is None:
            return torch.tensor(self.x[idx+24:idx+48].values, dtype=torch.float32).to(self.device)
        return torch.tensor(self.x[idx+24:idx+48].values, dtype=torch.float32).to(self.device), torch.tensor(self.y[idx+48], dtype=torch.float32).to(self.device)

In [102]:
class NNModel:
    def __init__(self, 
                 model: type[nn.Module], 
                 criterion: type[nn.modules.loss._Loss],
                 optimizer: type[torch.optim.Optimizer], 
                 area: str):
        self.model: type[nn.Module] = model
        self.criterion: type[nn.modules.loss._Loss] = criterion
        self.optimizer: type[torch.optim.Optimizer] = optimizer
        self.training_losses: list[float] = []
        self.validation_losses: list[float] = []
        if area in data_reader.mbas:
            self.area = area
        else:
            raise ValueError(f"{area} is not a valid area")
        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        self.model.to(self.device)
    
    def save(self,
             epoch: int | None = None, 
             final: bool = False):
        torch.save(
            {
                "state_dict": self.model.state_dict(), 
                "optimizer": self.optimizer.state_dict(),
                "epoch": epoch,
                "training_losses": self.training_losses,
                "validation_losses": self.validation_losses
            }, 
            f"models/{self.model}_area{self.area}_{'final' if final else f'epoch{epoch}'}.pth")
    
    def load(self, epoch: int | None = None, final: bool = False):
        checkpoint = torch.load(f"models/{self.model}_area{self.area}_{'final' if final else f'epoch{epoch}'}.pth")
        self.model.load_state_dict(checkpoint["state_dict"])
        self.model.to(self.device)
        self.optimizer.load_state_dict(checkpoint["optimizer"])
        self.training_losses: list[float] = checkpoint["training_losses"]
        self.validation_losses: list[float] = checkpoint["validation_losses"]
        return checkpoint["epoch"]

    def train(self, 
              train_data_loader: DataLoader, 
              epochs: int, 
              validation_data_loader: DataLoader, 
              validation_columns: list[str], 
              start_epoch: int = 0, 
              early_stopping: bool | int = False):
        
        min_val_loss = np.inf
        best_model: type[nn.Module] | None = None
        steps_since_improvement: int = 0
        self.model.eval()
        _, val_loss = self.validation(validation_data_loader, validation_columns)
        self.validation_losses.append(np.mean(val_loss))
        self.training_losses.append(np.mean(val_loss))

        epoch_iterator = tqdm(range(start_epoch, epochs), desc="Epoch", position=0)
        for epoch in epoch_iterator:
            # print(f"Epoch {epoch+1}/{epochs}:")
            self.model.train()
            training_loss= []
            # print("Training...")
            for x, y in tqdm(train_data_loader, desc="Training", position=1, leave=False):
                self.optimizer.zero_grad()
                outputs = self.model(x)
                loss = self.criterion(outputs.squeeze(), y)
                training_loss.append(loss.item())
                loss.backward()
                self.optimizer.step()
            self.training_losses.append(np.average(training_loss))
            print(f"Training loss: {np.mean(training_loss):.4f}")


            _, val_loss = self.validation(validation_data_loader, validation_columns)
            self.validation_losses.append(np.mean(val_loss))
            if early_stopping:
                if np.mean(val_loss) > min_val_loss:
                    steps_since_improvement += 1
                    if steps_since_improvement >= early_stopping:
                        print("Early stopping...")
                        self.model = best_model
                        epoch_iterator.close()
                        break
                else:
                    steps_since_improvement = 0
                    min_val_loss = np.mean(val_loss)
                    best_model = copy.deepcopy(self.model)
            if epoch % 5 == 0:
                self.save(epoch=epoch + 1)
        self.save(final=True)
        return self.training_losses, self.validation_losses 

    def validation(self, 
                   validation_data_loader: DataLoader,
                   columns: list[str],
                   use_previous_y_for_hours: int = 24):
        self.model.eval()
        losses = []
        outputs = []
        with torch.no_grad():
            # print("Validating...")
            for i, (x, y) in enumerate(tqdm(validation_data_loader, desc="Validation", position=1, leave=False)):
                for j in range(min(use_previous_y_for_hours, i)):
                    x[0, -j, columns.index('previous_y')] = outputs[-j] 
                    x[0, -j, columns.index('moving_24_avg_y')] = \
                        (torch.sum(x[0, :, columns.index('previous_y')]) + outputs[-j]) / 24
                output = self.model(x)
                loss = self.criterion(output.squeeze(0), y)
                losses.append(loss.item())
                outputs.append(output[0][0])
        print(f"Validation loss: {np.mean(losses):.4f}\n\n\n")
        return outputs, losses

In [99]:
def model_outputs(model: NNModel,
                  validation_data_loader: DataLoader,
                  columns: list[str],
                  use_previous_y_for_hours: int = 24):
    outputs, _ = model.validation(
        validation_data_loader=validation_data_loader,
        columns=columns,
        use_previous_y_for_hours=use_previous_y_for_hours)
    return torch.tensor(outputs, device = 'cpu')

def model_outputs_losses_df(
        model: NNModel,
        validation_data_loader: DataLoader,
        columns: list[str],
        scaler: StandardScaler,
        validation: pd.DataFrame,
        use_previous_y_for_hours: int = 24) -> tuple[pd.DataFrame, pd.DataFrame]:
    outputs = model_outputs(model=model,
                            validation_data_loader=validation_data_loader,
                            columns=columns,
                            use_previous_y_for_hours=use_previous_y_for_hours)
    outputs_actual_prev_y = model_outputs(model=model,
                                          validation_data_loader=validation_data_loader,
                                          columns=columns,
                                          use_previous_y_for_hours=0)
    validation_copy = validation.copy(deep=True)
    validation_copy0h = validation.copy(deep=True)
    validation_copy.loc[48:, (model.area, TARGET_VARIABLE)] = np.array(outputs).reshape(-1)
    validation_copy0h.loc[48:, (model.area, TARGET_VARIABLE)] = np.array(outputs_actual_prev_y).reshape(-1)

    validation_copy_unscaled = scaler.inverse_transform(validation_copy)
    validation_copy_unscaled0h = scaler.inverse_transform(validation_copy0h)
    val_output = pd.DataFrame(validation_copy_unscaled, columns=validation.columns, index=validation.index)
    val_output0h = pd.DataFrame(validation_copy_unscaled0h, columns=validation.columns, index=validation.index)

    # must slice off the first 48 hours because the model needs 24 hours of data to make a prediction, 
    # and all that data also needs 24 hours of data to create mean of last 24 hours
    df_outputs = pd.DataFrame({"Actual": validation[model.area][TARGET_VARIABLE][48:], 
                    "Predicted using predicted values for last 24 hours": val_output[model.area][TARGET_VARIABLE][48:], 
                    "Predicted using actual values for `target_y`": val_output0h[model.area][TARGET_VARIABLE][48:] })
    df_losses = pd.DataFrame({
        "Loss training": model.training_losses,
        "Loss validation using predicted values for last 24 hours": model.validation_losses
        })  
    return df_outputs, df_losses

def plot_unscaled_predictions(df, title):
    return px.line(df, x = df.index, y = df.columns).update_layout(xaxis_title="Time",
                        yaxis_title="MW",
                        title=title,
                        legend_title="") 
    
def plot_loss(loss_df, title):
    return px.line(loss_df, x = loss_df.index, y = loss_df.columns).update_layout(
        xaxis_title="Epochs",
        yaxis_title="MSE loss",
        title=title,
        legend_title="")

In [140]:
AREA = "NO1"
NUMBER_OF_COLUMNS = len(train[AREA].columns) - 1
VALIDATION_COLUMNS = list(validation[AREA].columns)

train_x = train[AREA].drop(columns=[TARGET_VARIABLE])
train_dl = DataLoader(EnergyDataset(train_x, train[AREA][TARGET_VARIABLE]), batch_size=64, shuffle=True)

val_x = val[AREA].drop(columns=[TARGET_VARIABLE])
val_dl = DataLoader(EnergyDataset(val_x, val[AREA][TARGET_VARIABLE]), batch_size=1, shuffle=False)
TRAIN = True

# LSTM

In [59]:
class RNNModel(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, num_layers, dropout=0):
        super(RNNModel, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.dropout = dropout
        self.lstm = nn.LSTM(input_size, hidden_size, num_layers, batch_first=True)
        self.fc = nn.Linear(hidden_size, output_size)
        self.dropout_layer = nn.Dropout(dropout)
        self.fc2 = nn.Linear(output_size, 1)

    def forward(self, x):
        h0 = torch.zeros(self.num_layers, x.size(0), self.hidden_size).to(torch.device("cuda" if torch.cuda.is_available() else "cpu"))
        c0 = torch.zeros(self.num_layers, x.size(0), self.hidden_size).to(torch.device("cuda" if torch.cuda.is_available() else "cpu"))
        out, _ = self.lstm(x, (h0, c0))
        out = torch.nn.functional.relu(self.fc(out[:, -1, :]))
        out = self.dropout_layer(out)
        out = self.fc2(out)
        return out                   
    
    def __str__(self) -> str:
        return  f"LSTM_hidden{self.hidden_size}_layers{self.num_layers}_dropout{self.dropout}"

In [141]:
# if hidden size is too big, then it will overfit
torch.manual_seed(42)
if TRAIN:
    for area in data_reader.mbas:
        lstm_torch_model = RNNModel(input_size=NUMBER_OF_COLUMNS, hidden_size=4, output_size=4, num_layers=1, dropout=0.2)
        lstm_optimizer = torch.optim.Adam(lstm_torch_model.parameters(), lr=1e-4, weight_decay=0.001)
        lstm_optimizer = torch.optim.SGD(lstm_torch_model.parameters(), lr=1e-4, weight_decay=0.001)
        
        lstm_criterion = nn.MSELoss()
        lstm_model = NNModel(model=lstm_torch_model, criterion=lstm_criterion, optimizer=lstm_optimizer, area=area)

        lstm_model.train(
            train_data_loader=train_dl,
            epochs=1000,
            validation_data_loader=val_dl,
            validation_columns=VALIDATION_COLUMNS,
            early_stopping=100)
else: 
    lstm_torch_model = RNNModel(input_size=NUMBER_OF_COLUMNS, hidden_size=2, output_size=1, num_layers=1)
    lstm_optimizer = torch.optim.Adam(lstm_torch_model.parameters(), lr=0.001, weight_decay=0.0001)
    lstm_criterion = nn.MSELoss()
    lstm_model = NNModel(model=lstm_torch_model, criterion=lstm_criterion, optimizer=lstm_optimizer, area=AREA)
    lstm_model.load(final=True)



Validation:   0%|          | 0/1391 [00:00<?, ?it/s]

Validation loss: 0.6535





Epoch:   0%|          | 0/1000 [00:00<?, ?it/s]

Training:   0%|          | 0/762 [00:00<?, ?it/s]

Training loss: 1.0908


...

Training loss: 0.3345


Validation:   0%|          | 0/1391 [00:00<?, ?it/s]

Validation loss: 0.2185





Training:   0%|          | 0/762 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [56]:
outputs_df_lstm, losses_df_lstm = model_outputs_losses_df(validation_data_loader=val_dl,
                                                          model=lstm_model,
                                                          columns=VALIDATION_COLUMNS,
                                                          scaler=scaler,
                                                          validation=validation)

Validation:   0%|          | 0/1391 [00:00<?, ?it/s]

Validation loss: 0.2639





Validation:   0%|          | 0/1391 [00:00<?, ?it/s]

Validation loss: 0.0287





<ipython-input-52-15a46fc6f6a1>:28: FutureWarning: Slicing a positional slice with .loc is not supported, and will raise TypeError in a future version.  Use .loc with labels or .iloc with positions instead.
  validation_copy.loc[48:, (model.area, TARGET_VARIABLE)] = np.array(outputs).reshape(-1)
<ipython-input-52-15a46fc6f6a1>:29: FutureWarning: Slicing a positional slice with .loc is not supported, and will raise TypeError in a future version.  Use .loc with labels or .iloc with positions instead.
  validation_copy0h.loc[48:, (model.area, TARGET_VARIABLE)] = np.array(outputs_actual_prev_y).reshape(-1)


In [54]:
plot_unscaled_predictions(outputs_df_lstm, "LSTM model predictions")

ModuleNotFoundError: No module named 'plotly.validators.layout'

In [28]:
plot_loss(losses_df_lstm, "LSTM model loss")

# CNN

In [133]:
class CNNModel(nn.Module):
    def __init__(self, input_size, channels, kernel_size, time_steps):
        super(CNNModel, self).__init__()
        self.kernel_size = kernel_size
        self.channels = channels
        self.time_steps = time_steps
        self.conv = nn.Conv1d(input_size, out_channels=channels, kernel_size=3, padding=1)
        self.avgpool = nn.AvgPool1d(2)
        self.bn = nn.BatchNorm1d(channels)
        self.fc = nn.Linear(int(channels*time_steps*0.5), input_size)
        self.dropout = nn.Dropout(0.2)
        self.fc2 = nn.Linear(input_size, 1)

    def forward(self, x):
        residual = x[:, -1, :]
        x = x.permute(0, 2, 1)
        x = torch.nn.functional.relu(self.conv(x))
        x = self.avgpool(x)
        x = self.bn(x)           
        x = x.view(x.size(0), -1)
        x = torch.nn.functional.relu(self.fc(x))
        x = self.dropout(x)
        x = x + residual
        x = self.fc2(x)
        return x                   
    
    def __str__(self) -> str:
        return  f"CONV1D_kernel{self.kernel_size}_channels{self.channels}_time_steps{self.time_steps}"

In [134]:
AREA = "NO5"
columns_to_drop = ["sin_dayofyear", "cos_dayofyear", "sin_day", "cos_day"]
columns_to_drop = []

train_cnn = train[AREA].drop(columns=columns_to_drop)
val_cnn = val[AREA].drop(columns=columns_to_drop)
NUMBER_OF_COLUMNS = len(train_cnn.columns) - 1
VALIDATION_COLUMNS = list(val_cnn.columns)

train_x = train_cnn.drop(columns=[TARGET_VARIABLE])
train_dl = DataLoader(EnergyDataset(train_x, train[AREA][TARGET_VARIABLE]), batch_size=128, shuffle=True)

val_x = val_cnn.drop(columns=[TARGET_VARIABLE])
val_dl = DataLoader(EnergyDataset(val_x, val[AREA][TARGET_VARIABLE]), batch_size=1, shuffle=False)
TRAIN = True

In [139]:
# overfitting with 20 channels, reducing to 5 to get better results
if TRAIN:
    for area in data_reader.mbas:
        cnn_torch_model = CNNModel(input_size=NUMBER_OF_COLUMNS, channels=10, kernel_size=3, time_steps=24)
        cnn_optimizer = torch.optim.Adam(cnn_torch_model.parameters(), lr=1e-4, weight_decay=0.0001)
        cnn_optimizer = torch.optim.SGD(cnn_torch_model.parameters(), lr=1e-4, weight_decay=0.0001)

        cnn_criterion = nn.MSELoss()
        cnn_model = NNModel(model=cnn_torch_model, criterion=cnn_criterion, optimizer=cnn_optimizer, area=area)

        cnn_model.train(
            train_data_loader=train_dl,
            epochs=1000,
            validation_data_loader=val_dl,
            validation_columns=VALIDATION_COLUMNS,
            early_stopping=100)
else: 
    cnn_torch_model = CNNModel(input_size=NUMBER_OF_COLUMNS, channels=10, kernel_size=3, time_steps=24)
    cnn_optimizer = torch.optim.Adam(cnn_torch_model.parameters(), lr=1e-4, weight_decay=0.0001)
    cnn_optimizer = torch.optim.SGD(cnn_torch_model.parameters(), lr=1e-4, weight_decay=0.0001)

    cnn_criterion = nn.MSELoss()
    cnn_model = NNModel(model=cnn_torch_model, criterion=cnn_criterion, optimizer=cnn_optimizer, area=AREA)
    cnn_model.load(final=True)


Validation:   0%|          | 0/1391 [00:00<?, ?it/s]

Validation loss: 2.4392





Epoch:   0%|          | 0/1000 [00:00<?, ?it/s]

Training:   0%|          | 0/381 [00:00<?, ?it/s]

Training loss: 0.4645


...

Validation loss: 0.0687





Training:   0%|          | 0/381 [00:00<?, ?it/s]

Training loss: 0.0194


Validation:   0%|          | 0/1391 [00:00<?, ?it/s]

Validation loss: 0.0692





In [ ]:
outputs_df_cnn, losses_df_cnn = model_outputs_losses_df(validation_data_loader=val_dl,
                                                        model=cnn_model,
                                                        columns=VALIDATION_COLUMNS,
                                                        scaler=scaler,
                                                        validation=validation)

In [29]:
plot_unscaled_predictions(outputs_df_cnn, "CNN model predictions")

In [16]:
plot_loss(losses_df_cnn, "CNN model loss")